# Table of Contents
 <p>

In [1]:
#!/usr/bin/python

import pandas as pd
import dask.dataframe as dd
import datashader as ds
import datashader.transfer_functions as tf
from datashader.colors import colormap_select, Hot, viridis
from datashader.utils import export_image

from pyproj import Proj, transform

from datashader.bokeh_ext import InteractiveImage, create_ramp_legend
from bokeh.tile_providers import WMTSTileSource, STAMEN_TERRAIN
from bokeh.plotting import figure, output_notebook, output_file, show
from IPython.core.display import HTML, display
from bokeh.embed import file_html

from functools import partial

output_notebook()


# Define Dataset as pandas dataframe
df = pd.read_hdf('POAK_AIS.hdf5','AIS-in')
#df = pd.read_csv('Test.csv')

# WGS 84
inProj = Proj(init='epsg:4326')

# Web mercator 
outProj = Proj(init='epsg:3857')

# Re-project!
df['xWeb'],df['yWeb'] = transform(inProj,outProj,df['X'].values,df['Y'].values)


plot_width  = 1000
plot_height = 800
x_range = (df.xWeb.min(),df.xWeb.max())
y_range = (df.yWeb.min(),df.yWeb.max())
POSF = (x_range,y_range)

tools = ['wheel_zoom','save']
def base_plot(tools='pan,wheel_zoom,reset',plot_width=plot_width, plot_height=plot_height, **plot_args):
    p = figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
        x_range=x_range, y_range=y_range, outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0, **plot_args)

    p.axis.visible = False
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p
    
options = dict(line_color=None, fill_color='blue', size=5)

background = "black"
export = partial(export_image, export_path="export", background=background)
cm = partial(colormap_select, reverse=(background=="black"))

def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(df, 'xWeb', 'yWeb',ds.mean('SOG'))
    
    img = tf.shade(agg, cmap=viridis, how='eq_hist',alpha=150)
    
    fig = tf.dynspread(img, threshold=0.5, max_px=4)
    
    return fig

def create_legend(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(df, 'xWeb', 'yWeb',ds.mean('SOG'))
    legend_fig = create_ramp_legend(agg,viridis,width=900)
    return legend_fig

p = base_plot()
p.add_tile(STAMEN_TERRAIN)


#export(create_image(*POSF),"POSF")
# this is where the magic happens
#output_file('HiThere.html')
#show(p)
InteractiveImage(p, create_image)


Loading BokehJS ...